# Черновик - содержит различные варианты

In [1]:
import numpy as np
import pandas as pd

import warnings
warnings.filterwarnings('ignore')

### 1) Читаем данные

In [2]:
data = pd.read_csv('input/train.csv')

In [3]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 20 columns):
Id               10000 non-null int64
DistrictId       10000 non-null int64
Rooms            10000 non-null float64
Square           10000 non-null float64
LifeSquare       7887 non-null float64
KitchenSquare    10000 non-null float64
Floor            10000 non-null int64
HouseFloor       10000 non-null float64
HouseYear        10000 non-null int64
Ecology_1        10000 non-null float64
Ecology_2        10000 non-null object
Ecology_3        10000 non-null object
Social_1         10000 non-null int64
Social_2         10000 non-null int64
Social_3         10000 non-null int64
Healthcare_1     5202 non-null float64
Helthcare_2      10000 non-null int64
Shops_1          10000 non-null int64
Shops_2          10000 non-null object
Price            10000 non-null float64
dtypes: float64(8), int64(9), object(3)
memory usage: 1.5+ MB


In [4]:
data.head()

Id  DistrictId  Rooms     Square  LifeSquare  KitchenSquare  Floor  \
0  14038          35    2.0  47.981561   29.442751            6.0      7   
1  15053          41    3.0  65.683640   40.049543            8.0      7   
2   4765          53    2.0  44.947953   29.197612            0.0      8   
3   5809          58    2.0  53.352981   52.731512            9.0      8   
4  10783          99    1.0  39.649192   23.776169            7.0     11   

   HouseFloor  HouseYear  Ecology_1 Ecology_2 Ecology_3  Social_1  Social_2  \
0         9.0       1969   0.089040         B         B        33      7976   
1         9.0       1978   0.000070         B         B        46     10309   
2        12.0       1968   0.049637         B         B        34      7759   
3        17.0       1977   0.437885         B         B        23      5735   
4        12.0       1976   0.012339         B         B        35      5776   

   Social_3  Healthcare_1  Helthcare_2  Shops_1 Shops_2          Price  
0         5           NaN            0       11       B  184966.930730  
1         1         240.0            1       16       B  300009.450063  
2         0         229.0            1        3       B  220925.908524  
3         3        1084.0            0        5       B  175616.227217  
4         1        2078.0            2        4       B  150226.531644

### 2) Разбиваем на трейн и валид

In [5]:
from sklearn.model_selection import train_test_split

In [6]:
train, valid = train_test_split(data, test_size=0.3, random_state=42)

In [7]:
train.columns

Index(['Id', 'DistrictId', 'Rooms', 'Square', 'LifeSquare', 'KitchenSquare',
       'Floor', 'HouseFloor', 'HouseYear', 'Ecology_1', 'Ecology_2',
       'Ecology_3', 'Social_1', 'Social_2', 'Social_3', 'Healthcare_1',
       'Helthcare_2', 'Shops_1', 'Shops_2', 'Price'],
      dtype='object')

### 3) Пишем функции для обработки данных

In [8]:
def clean_rooms(df):
    df.loc[df['Rooms'] > 5, 'Rooms'] = 5
    return df

In [9]:
def clean_square(df):
    df.loc[df['Square'] < 15, 'Square'] = 15
    df['LifeSquare'] = df['LifeSquare'].fillna(df['Square'] - df['KitchenSquare'])
    df.loc[df['Square'] < df['LifeSquare'] + df['KitchenSquare'], 'Square'] = df['LifeSquare'] + df['KitchenSquare']
    return df

In [10]:
def clean_year(df):
    df.loc[df['HouseYear'] > 2020, 'HouseYear'] = 2020
    return df

In [11]:
stat1 = train.groupby(['DistrictId', 'Rooms'], as_index=False)[['Price']].mean().rename(columns={'Price':'mean_price_dr'})
stat2 = train.groupby(['Rooms'], as_index=False)[['Price']].mean().rename(columns={'Price':'mean_price_r'})
mean_price = train['Price'].mean()

In [12]:
def add_mean_price(df, stat1, stat2, mean_price):
    df = pd.merge(df, stat1, on=['DistrictId', 'Rooms'], how='left')
    df = pd.merge(df, stat2, on=['Rooms'], how='left')
    df['mean_price_r'] = df['mean_price_r'].fillna(mean_price)
    df['mean_price_dr'] = df['mean_price_dr'].fillna(df['mean_price_r'])
    return df

In [13]:
def remove_strings(df):
    df = pd.get_dummies(df, columns = ['Ecology_2', 'Ecology_3', 'Shops_2'])
    return df

In [14]:
def prepare_data(df, stat1=stat1, stat2=stat2, mean_price=mean_price):
    df = clean_rooms(df)
    df = clean_square(df)
    df = clean_year(df)
    df = add_mean_price(df, stat1, stat2, mean_price)
    df = remove_strings(df)
    df = df.drop(columns='Healthcare_1')
    return df

### 4) Чистка данных

In [15]:
train.describe()

Id   DistrictId        Rooms       Square   LifeSquare  \
count   7000.000000  7000.000000  7000.000000  7000.000000  5514.000000   
mean    8386.061714    50.560857     1.889286    56.307485    37.523283   
std     4864.141324    43.744178     0.843116    20.507466   102.071817   
min        0.000000     0.000000     0.000000     2.377248     0.370619   
25%     4176.500000    19.000000     1.000000    41.744710    22.766442   
50%     8398.500000    37.000000     2.000000    52.633656    32.868499   
75%    12562.000000    75.000000     2.000000    65.981105    45.121115   
max    16796.000000   209.000000    19.000000   604.705972  7480.592129   

       KitchenSquare        Floor   HouseFloor     HouseYear    Ecology_1  \
count    7000.000000  7000.000000  7000.000000  7.000000e+03  7000.000000   
mean        6.490714     8.521286    12.654571  4.849634e+03     0.117840   
std        33.999713     5.222043     6.851357  2.396436e+05     0.118599   
min         0.000000     1.000000     0.000000  1.912000e+03     0.000000   
25%         1.000000     4.000000     9.000000  1.974000e+03     0.017647   
50%         6.000000     7.000000    14.000000  1.977000e+03     0.075424   
75%         9.000000    12.000000    17.000000  2.001000e+03     0.194489   
max      2014.000000    42.000000   117.000000  2.005201e+07     0.521867   

          Social_1      Social_2     Social_3  Healthcare_1  Helthcare_2  \
count  7000.000000   7000.000000  7000.000000   3642.000000  7000.000000   
mean     24.767571   5364.425714     8.044571   1133.876167     1.313143   
std      17.583889   4011.768297    23.869975   1018.354716     1.488326   
min       0.000000    168.000000     0.000000     30.000000     0.000000   
25%       6.000000   1564.000000     0.000000    325.000000     0.000000   
50%      25.000000   5285.000000     2.000000    900.000000     1.000000   
75%      36.000000   7227.000000     5.000000   1548.000000     2.000000   
max      74.000000  19083.000000   141.000000   4849.000000     6.000000   

           Shops_1          Price  
count  7000.000000    7000.000000  
mean      4.260571  214449.167390  
std       4.825024   92924.798790  
min       0.000000   59174.778028  
25%       1.000000  154599.240157  
50%       3.000000  192290.039215  
75%       6.000000  249080.956886  
max      23.000000  627525.072788

In [16]:
train[train['Rooms'] < 1]

Id  DistrictId  Rooms      Square  LifeSquare  KitchenSquare  Floor  \
4366    456           6    0.0   81.491446         NaN            0.0      4   
1397  12638          27    0.0  138.427694  136.215499            0.0      4   
2269   7317          27    0.0   41.790881         NaN            0.0     13   
3911    770          28    0.0   49.483501         NaN            0.0     16   
4853   3224          27    0.0    2.377248    0.873147            0.0      1   

      HouseFloor  HouseYear  Ecology_1 Ecology_2 Ecology_3  Social_1  \
4366         0.0       1977   0.243205         B         B         5   
1397         3.0       2016   0.075424         B         B        11   
2269         0.0       1977   0.211401         B         B         9   
3911         0.0       2015   0.118537         B         B        30   
4853         0.0       1977   0.017647         B         B         2   

      Social_2  Social_3  Healthcare_1  Helthcare_2  Shops_1 Shops_2  \
4366      1564         0         540.0            0        0       B   
1397      3097         0           NaN            0        0       B   
2269      1892         0           NaN            0        1       B   
3911      6207         1        1183.0            1        0       B   
4853       469         0           NaN            0        0       B   

              Price  
4366  212864.799112  
1397  268394.744389  
2269   98129.976788  
3911  217009.338463  
4853  126596.941798

### 5) Применяем функции на трейне и валиде

In [17]:
train = prepare_data(train)
valid = prepare_data(valid)

### 6) Строим модель, делаем предсказание на трейне и валиде

In [18]:
from sklearn.ensemble import RandomForestRegressor as RF

In [19]:
model = RF(n_estimators=25, max_depth=10, random_state=42)

In [20]:
feats = ['Rooms', 'Square', 'HouseYear', 'mean_price_dr']

In [21]:
model.fit(train.loc[:, feats], train['Price'])

RandomForestRegressor(bootstrap=True, criterion='mse', max_depth=10,
           max_features='auto', max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=1, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators=25, n_jobs=1,
           oob_score=False, random_state=42, verbose=0, warm_start=False)

### 7) Проверяем качество модели

In [22]:
from sklearn.metrics import r2_score

In [23]:
def pred_evaluate_model(df, model=model, feats=feats, calculate_r2='Yes'):
    pred = model.predict(df.loc[:, feats])
    if calculate_r2 == 'Yes':
        r2 = r2_score(df['Price'], pred)
        print(f'R2: {r2}')
    return pred

In [24]:
def evaluate_model(df, model=model, feats=feats):
    pred = model.predict(df.loc[:, feats])
    return r2_score(df['Price'], pred)

In [25]:
pred_train = pred_evaluate_model(train)

R2: 0.8686079229633344


In [26]:
pred_valid = pred_evaluate_model(valid)

R2: 0.6619841359378945


### 7.5) Исследование, что лучше подойдёт

#### Линейная регрессия

In [27]:
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler

In [28]:
def check_regression(feats, train=train, valid=valid, do_scalar=True):
    lr = LinearRegression()
    scaler = StandardScaler()
    X_train = train.loc[:, feats]
    y_train = train['Price']
    X_valid = valid.loc[:, feats]
    y_valid = valid['Price']
    if do_scalar:
        X_train = pd.DataFrame(data=scaler.fit_transform(X_train), columns=feats)
        X_valid = pd.DataFrame(data=scaler.transform(X_valid), columns=feats)
    lr.fit(X_train, y_train)
    X_train['Price'] = y_train
    X_valid['Price'] = y_valid
    return f"{evaluate_model(X_train, model=lr, feats=feats)}" \
           f"\t{evaluate_model(X_valid, model=lr, feats=feats)}" \
           f"\t{feats}\t{do_scalar}"

In [29]:
print(check_regression(['Rooms', 'Square', 'HouseYear', 'mean_price_r']))

0.3352179935572549	0.326627168546189	['Rooms', 'Square', 'HouseYear', 'mean_price_r']	True


In [30]:
from sklearn.ensemble import RandomForestRegressor as RF

In [31]:
def check_forest(feats, n_estimators, max_depth, train=train, valid=valid):
    model = RF(n_estimators=n_estimators, max_depth=max_depth, random_state=42)
    model.fit(train.loc[:, feats], train['Price'])
    return f"{evaluate_model(train, model=model, feats=feats)}" \
           f"\t{evaluate_model(valid, model=model, feats=feats)}" \
           f"\t{n_estimators}\t{max_depth}"

In [32]:
def check_forests(feats, train=train, valid=valid):
    for i in range(50):
        for j in range(30):
            try:
                model = RF(n_estimators=i+1, max_depth=j+1, random_state=42)
                model.fit(train.loc[:, feats], train['Price'])
                print(f"{evaluate_model(train, model=model, feats=feats)}" \
                      f"\t{evaluate_model(valid, model=model, feats=feats)}" \
                      f"\t{i+1}\t{j+1}")
            except:
                print(f"Cant\t{i+1}\t{j+1}")
    

In [33]:
import itertools

In [34]:
possible_feats = list(train.columns.values)
possible_feats.remove('Price')
possible_feats.remove('Id')
possible_feats.remove('Healthcare_1')

In [65]:
train.corr()['Price']

Id               0.019332
DistrictId       0.264105
Rooms            0.570405
Square           0.107811
LifeSquare       0.068150
KitchenSquare    0.020301
Floor            0.126098
HouseFloor       0.089321
HouseYear        0.035236
Ecology_1       -0.064129
Social_1         0.265278
Social_2         0.240089
Social_3         0.076234
Helthcare_2      0.253601
Shops_1          0.183545
Price            1.000000
mean_price_dr    0.813599
mean_price_r     0.575864
Ecology_2_A     -0.030568
Ecology_2_B      0.030568
Ecology_3_A      0.051992
Ecology_3_B     -0.051992
Shops_2_A       -0.061129
Shops_2_B        0.061129
Name: Price, dtype: float64

In [131]:
possible_feats = train.corr()['Price'][abs(train.corr()['Price']) > 0.25].index
possible_feats = list(possible_feats)
possible_feats.remove('Price')

In [132]:
print(possible_feats)

['DistrictId', 'Rooms', 'Social_1', 'Helthcare_2', 'mean_price_dr', 'mean_price_r']


In [ ]:
for i in range(len(possible_feats)):
    for j in list(itertools.combinations(possible_feats, i+1)):
        try:
            print(check_regression(j))
            print(check_regression(j, do_scalar=False))
        except:
            pass
    

0.00037371638876326774	-0.000971101335881297	('Id',)	True
0.00037371638876326774	-0.000971101335881297	('Id',)	False
0.06975166747927108	0.07140094716263345	('DistrictId',)	True
0.06975166747927108	0.07140094716263345	('DistrictId',)	False
0.3253620115013037	0.3190890790865729	('Rooms',)	True
0.32536201150130384	0.3190890790865729	('Rooms',)	False
0.011623270095029392	0.02350339710100302	('Square',)	True
0.011623270095029392	0.02350339710100302	('Square',)	False
0.0004121105954596471	0.001232266828357087	('KitchenSquare',)	True
0.00041211059545975814	0.001232266828357087	('KitchenSquare',)	False
0.015900788755261908	0.017988940712757584	('Floor',)	True
0.015900788755261908	0.017988940712757584	('Floor',)	False
0.00797827802801343	0.0072483958417818295	('HouseFloor',)	True
0.00797827802801343	0.0072483958417818295	('HouseFloor',)	False
0.0012415883873856393	0.0014745592228435633	('HouseYear',)	True
0.0012415883873856393	0.0014745592228436744	('HouseYear',)	False
0.004112582680205201	0.0

0.008419103703040665	0.008574027964706854	('KitchenSquare', 'HouseFloor')	True
0.008419103703040665	0.008574027964706965	('KitchenSquare', 'HouseFloor')	False
0.0016011880892636832	0.002711320387298599	('KitchenSquare', 'HouseYear')	True
0.0016011880892636832	0.002711320387298488	('KitchenSquare', 'HouseYear')	False
0.004506303463887473	0.0028588839754807305	('KitchenSquare', 'Ecology_1')	True
0.004506303463887584	0.0028588839754807305	('KitchenSquare', 'Ecology_1')	False
0.07049619131999063	0.06726101921420202	('KitchenSquare', 'Social_1')	True
0.07049619131999063	0.06726101921420202	('KitchenSquare', 'Social_1')	False
0.05781875891945054	0.05680500028384172	('KitchenSquare', 'Social_2')	True
0.05781875891945054	0.05680500028384161	('KitchenSquare', 'Social_2')	False
0.006269541060237804	0.006453575729278627	('KitchenSquare', 'Social_3')	True
0.006269541060237804	0.006453575729278738	('KitchenSquare', 'Social_3')	False
0.06440353147284172	0.0638293564783714	('KitchenSquare', 'Helthcar

0.33686095272320893	0.3266110379958673	('Social_3', 'mean_price_r')	True
0.33686095272320904	0.32661103799586744	('Social_3', 'mean_price_r')	False
0.06946191251295775	0.06722106176492826	('Helthcare_2', 'Shops_1')	True
0.06946191251295775	0.06722106176492826	('Helthcare_2', 'Shops_1')	False
-54622044213.99224	-54349076249.219154	('Helthcare_2', 'Price')	True
1.0	1.0	('Helthcare_2', 'Price')	False
0.6621762946177471	0.5195741424647109	('Helthcare_2', 'mean_price_dr')	True
0.6621762946177472	0.5195741424647109	('Helthcare_2', 'mean_price_dr')	False
0.37733713165029925	0.3745037988477814	('Helthcare_2', 'mean_price_r')	True
0.37733713165029914	0.3745037988477814	('Helthcare_2', 'mean_price_r')	False
-54622044213.99241	-54349076249.21932	('Shops_1', 'Price')	True
1.0	1.0	('Shops_1', 'Price')	False
0.6621088014351487	0.519350791894592	('Shops_1', 'mean_price_dr')	True
0.6621088014351486	0.519350791894592	('Shops_1', 'mean_price_dr')	False
0.3537049498092423	0.34630723323184687	('Shops_1', 

0.06476651299861291	0.06292851656371168	('Id', 'KitchenSquare', 'Helthcare_2')	True
0.06476651299861291	0.06292851656371168	('Id', 'KitchenSquare', 'Helthcare_2')	False
0.03447245629362006	0.030582220875249422	('Id', 'KitchenSquare', 'Shops_1')	True
0.03447245629362017	0.030582220875249422	('Id', 'KitchenSquare', 'Shops_1')	False
-54622044213.99235	-54349076249.21927	('Id', 'KitchenSquare', 'Price')	True
1.0	1.0	('Id', 'KitchenSquare', 'Price')	False
0.6620274453124673	0.5188351719970353	('Id', 'KitchenSquare', 'mean_price_dr')	True
0.6620274453124673	0.5188351719970354	('Id', 'KitchenSquare', 'mean_price_dr')	False
0.33217109522806054	0.3246672084001726	('Id', 'KitchenSquare', 'mean_price_r')	True
0.33217109522806065	0.3246672084001728	('Id', 'KitchenSquare', 'mean_price_r')	False
0.017949852788163634	0.017975911128676914	('Id', 'Floor', 'HouseFloor')	True
0.017949852788163634	0.017975911128677247	('Id', 'Floor', 'HouseFloor')	False
0.01629705510794044	0.017030316436446147	('Id', 'Flo

0.3370779876342399	0.3268244628565605	('Id', 'Social_3', 'mean_price_r')	True
0.3370779876342398	0.3268244628565605	('Id', 'Social_3', 'mean_price_r')	False
0.06986752758307369	0.06629460038792334	('Id', 'Helthcare_2', 'Shops_1')	True
0.06986752758307369	0.06629460038792367	('Id', 'Helthcare_2', 'Shops_1')	False
-54622044213.99233	-54349076249.21926	('Id', 'Helthcare_2', 'Price')	True
1.0	1.0	('Id', 'Helthcare_2', 'Price')	False
0.6622512940641361	0.5195582320111345	('Id', 'Helthcare_2', 'mean_price_dr')	True
0.6622512940641361	0.5195582320111263	('Id', 'Helthcare_2', 'mean_price_dr')	False
0.3775344238461432	0.3746612939356858	('Id', 'Helthcare_2', 'mean_price_r')	True
0.3775344238461431	0.37466129393569114	('Id', 'Helthcare_2', 'mean_price_r')	False
-54622044213.99232	-54349076249.21924	('Id', 'Shops_1', 'Price')	True
1.0	1.0	('Id', 'Shops_1', 'Price')	False
0.6621857783190708	0.519339123471834	('Id', 'Shops_1', 'mean_price_dr')	True
0.6621857783190708	0.5193391234718338	('Id', 'Shop

...

0.38956654132240853	0.378956553035496	('Rooms', 'Square', 'HouseYear', 'Social_1', 'Social_2', 'Social_3')	True
0.38956654132240853	0.37895655303549625	('Rooms', 'Square', 'HouseYear', 'Social_1', 'Social_2', 'Social_3')	False
0.3968742999414787	0.39268266076608016	('Rooms', 'Square', 'HouseYear', 'Social_1', 'Social_2', 'Helthcare_2')	True
0.3968742999414787	0.39268266076608016	('Rooms', 'Square', 'HouseYear', 'Social_1', 'Social_2', 'Helthcare_2')	False
0.38558240067292826	0.37784356563571064	('Rooms', 'Square', 'HouseYear', 'Social_1', 'Social_2', 'Shops_1')	True
0.38558240067292837	0.37784356563571064	('Rooms', 'Square', 'HouseYear', 'Social_1', 'Social_2', 'Shops_1')	False
-54622044213.99235	-54349076249.21927	('Rooms', 'Square', 'HouseYear', 'Social_1', 'Social_2', 'Price')	True
1.0	1.0	('Rooms', 'Square', 'HouseYear', 'Social_1', 'Social_2', 'Price')	False
0.6750098468989842	0.5307539196323408	('Rooms', 'Square', 'HouseYear', 'Social_1', 'Social_2', 'mean_price_dr')	True
0.67500

-54622044213.99252	-54349076249.21945	('Rooms', 'Square', 'HouseYear', 'Social_3', 'Helthcare_2', 'Price')	True
1.0	1.0	('Rooms', 'Square', 'HouseYear', 'Social_3', 'Helthcare_2', 'Price')	False
0.6751731769749957	0.5315534455517366	('Rooms', 'Square', 'HouseYear', 'Social_3', 'Helthcare_2', 'mean_price_dr')	True
0.6751731769749957	0.5315534455517364	('Rooms', 'Square', 'HouseYear', 'Social_3', 'Helthcare_2', 'mean_price_dr')	False
0.3845482603842735	0.38122374936715475	('Rooms', 'Square', 'HouseYear', 'Social_3', 'Helthcare_2', 'mean_price_r')	True
0.3845482603842735	0.3812237493671544	('Rooms', 'Square', 'HouseYear', 'Social_3', 'Helthcare_2', 'mean_price_r')	False
-54622044213.99241	-54349076249.21932	('Rooms', 'Square', 'HouseYear', 'Social_3', 'Shops_1', 'Price')	True
1.0	1.0	('Rooms', 'Square', 'HouseYear', 'Social_3', 'Shops_1', 'Price')	False
0.6747087313453818	0.5298285837670283	('Rooms', 'Square', 'HouseYear', 'Social_3', 'Shops_1', 'mean_price_dr')	True
0.6747087313453819	0.

0.38610559776503195	0.38376113535642264	('Rooms', 'Square', 'Ecology_1', 'Social_2', 'Helthcare_2', 'Shops_1')	False
-54622044213.99242	-54349076249.219345	('Rooms', 'Square', 'Ecology_1', 'Social_2', 'Helthcare_2', 'Price')	True
1.0	1.0	('Rooms', 'Square', 'Ecology_1', 'Social_2', 'Helthcare_2', 'Price')	False
0.6636044065187878	0.5224668619897095	('Rooms', 'Square', 'Ecology_1', 'Social_2', 'Helthcare_2', 'mean_price_dr')	True
0.6636044065187878	0.5224668619896972	('Rooms', 'Square', 'Ecology_1', 'Social_2', 'Helthcare_2', 'mean_price_dr')	False
0.39201443023516913	0.38824258476352147	('Rooms', 'Square', 'Ecology_1', 'Social_2', 'Helthcare_2', 'mean_price_r')	True
0.39201443023516913	0.3882425847635186	('Rooms', 'Square', 'Ecology_1', 'Social_2', 'Helthcare_2', 'mean_price_r')	False
-54622044213.992455	-54349076249.21938	('Rooms', 'Square', 'Ecology_1', 'Social_2', 'Shops_1', 'Price')	True
1.0	1.0	('Rooms', 'Square', 'Ecology_1', 'Social_2', 'Shops_1', 'Price')	False
0.66353009397041

-54622044213.992294	-54349076249.21922	('Rooms', 'Square', 'Social_1', 'Social_2', 'Price', 'mean_price_dr')	True
1.0	1.0	('Rooms', 'Square', 'Social_1', 'Social_2', 'Price', 'mean_price_dr')	False
-54622044213.99232	-54349076249.21924	('Rooms', 'Square', 'Social_1', 'Social_2', 'Price', 'mean_price_r')	True
1.0	1.0	('Rooms', 'Square', 'Social_1', 'Social_2', 'Price', 'mean_price_r')	False
0.6631900458397919	0.5216009824635054	('Rooms', 'Square', 'Social_1', 'Social_2', 'mean_price_dr', 'mean_price_r')	True
0.6631900458397919	0.5216009824635073	('Rooms', 'Square', 'Social_1', 'Social_2', 'mean_price_dr', 'mean_price_r')	False
0.38894536194029816	0.3851489458333379	('Rooms', 'Square', 'Social_1', 'Social_3', 'Helthcare_2', 'Shops_1')	True
0.38894536194029816	0.3851489458333379	('Rooms', 'Square', 'Social_1', 'Social_3', 'Helthcare_2', 'Shops_1')	False
-54622044213.99235	-54349076249.21927	('Rooms', 'Square', 'Social_1', 'Social_3', 'Helthcare_2', 'Price')	True
1.0	1.0	('Rooms', 'Square'

-54622044213.9922	-54349076249.21912	('Rooms', 'Square', 'Social_3', 'Helthcare_2', 'Shops_1', 'Price')	True
1.0	1.0	('Rooms', 'Square', 'Social_3', 'Helthcare_2', 'Shops_1', 'Price')	False
0.6630427253273834	0.5216600128757821	('Rooms', 'Square', 'Social_3', 'Helthcare_2', 'Shops_1', 'mean_price_dr')	True
0.6630427253273834	0.5216600128757821	('Rooms', 'Square', 'Social_3', 'Helthcare_2', 'Shops_1', 'mean_price_dr')	False
0.38159947798555527	0.38016342424827154	('Rooms', 'Square', 'Social_3', 'Helthcare_2', 'Shops_1', 'mean_price_r')	True
0.38159947798555516	0.3801634242482711	('Rooms', 'Square', 'Social_3', 'Helthcare_2', 'Shops_1', 'mean_price_r')	False
-54622044213.99239	-54349076249.219315	('Rooms', 'Square', 'Social_3', 'Helthcare_2', 'Price', 'mean_price_dr')	True
1.0	1.0	('Rooms', 'Square', 'Social_3', 'Helthcare_2', 'Price', 'mean_price_dr')	False
-54622044213.99232	-54349076249.21924	('Rooms', 'Square', 'Social_3', 'Helthcare_2', 'Price', 'mean_price_r')	True
1.0	1.0	('Rooms'

In [76]:
from sklearn.feature_selection import SelectKBest, f_regression

In [77]:
train.drop(columns='Price').shape

(7000, 23)

In [78]:
train['Price'].shape

(7000,)

In [79]:
kbest_model = SelectKBest(score_func=f_regression, k=4)

In [80]:
kbest = kbest_model.fit(train.drop(columns='Price'), train['Price'])

In [83]:
scores = pd.DataFrame(kbest.scores_)
scores['Name'] = train.drop(columns='Price').columns.values

In [84]:
scores

0           Name
0       2.616245             Id
1     524.722434     DistrictId
2    3374.970570          Rooms
3      82.296195         Square
4      32.653477     LifeSquare
5       2.885139  KitchenSquare
6     113.071648          Floor
7      56.281015     HouseFloor
8       8.699437      HouseYear
9      28.898702      Ecology_1
10    529.744623       Social_1
11    428.057740       Social_2
12     40.907608       Social_3
13    481.000462    Helthcare_2
14    243.973138        Shops_1
15  13702.643319  mean_price_dr
16   3472.081182   mean_price_r
17      6.545252    Ecology_2_A
18      6.545252    Ecology_2_B
19     18.968202    Ecology_3_A
20     18.968202    Ecology_3_B
21     26.247769      Shops_2_A
22     26.247769      Shops_2_B

In [31]:
from sklearn.feature_selection import RFE
from sklearn.linear_model import LogisticRegression
from sklearn import preprocessing

In [32]:
model = LogisticRegression()

In [33]:
rfe = RFE(model, 6)

In [32]:
lab_enc = preprocessing.LabelEncoder()
training_scores_encoded = lab_enc.fit_transform(train.loc[:, 'Price'])

In [ ]:
fit = rfe.fit(train.drop(columns='Price'), training_scores_encoded)

In [33]:
from sklearn.decomposition import PCA

In [35]:
X_train = train.drop(columns='Price')
y_train = train.loc[:, 'Price']

In [34]:
def do_pca(pca_comp, train=train, valid=valid):
    pca_feats = list('abcdefghijklmnopqrstuvwxyz'[0:pca_comp])
    pca = PCA(n_components=pca_comp)
    fit = pca.fit(train.drop(columns='Price'))
    X_train_pca = fit.transform(train.drop(columns='Price'))
    X_train_pca = pd.DataFrame(X_train_pca, columns=pca_feats)
    X_train_pca['Price'] = train['Price']
    X_valid_pca = fit.transform(valid.drop(columns='Price'))
    X_valid_pca = pd.DataFrame(X_valid_pca, columns=pca_feats)
    X_valid_pca['Price'] = valid.loc[:, 'Price']
    check_forests(pca_feats, train=X_train_pca, valid=X_valid_pca)    

In [ ]:
for i in range(15):
    do_pca(i)

Cant	1	1
Cant	1	2
Cant	1	3
Cant	1	4
Cant	1	5
Cant	1	6
Cant	1	7
Cant	1	8
Cant	1	9
Cant	1	10
Cant	1	11
Cant	1	12
Cant	1	13
Cant	1	14
Cant	1	15
Cant	1	16
Cant	1	17
Cant	1	18
Cant	1	19
Cant	1	20
Cant	1	21
Cant	1	22
Cant	1	23
Cant	1	24
Cant	1	25
Cant	1	26
Cant	1	27
Cant	1	28
Cant	1	29
Cant	1	30
Cant	2	1
Cant	2	2
Cant	2	3
Cant	2	4
Cant	2	5
Cant	2	6
Cant	2	7
Cant	2	8
Cant	2	9
Cant	2	10
Cant	2	11
Cant	2	12
Cant	2	13
Cant	2	14
Cant	2	15
Cant	2	16
Cant	2	17
Cant	2	18
Cant	2	19
Cant	2	20
Cant	2	21
Cant	2	22
Cant	2	23
Cant	2	24
Cant	2	25
Cant	2	26
Cant	2	27
Cant	2	28
Cant	2	29
Cant	2	30
Cant	3	1
Cant	3	2
Cant	3	3
Cant	3	4
Cant	3	5
Cant	3	6
Cant	3	7
Cant	3	8
Cant	3	9
Cant	3	10
Cant	3	11
Cant	3	12
Cant	3	13
Cant	3	14
Cant	3	15
Cant	3	16
Cant	3	17
Cant	3	18
Cant	3	19
Cant	3	20
Cant	3	21
Cant	3	22
Cant	3	23
Cant	3	24
Cant	3	25
Cant	3	26
Cant	3	27
Cant	3	28
Cant	3	29
Cant	3	30
Cant	4	1
Cant	4	2
Cant	4	3
Cant	4	4
Cant	4	5
Cant	4	6
Cant	4	7
Cant	4	8
Cant	4	9
Cant	4	10
Cant	4	11
Cant	4	12
Cant	4	13
Cant	4

Cant	28	26
Cant	28	27
Cant	28	28
Cant	28	29
Cant	28	30
Cant	29	1
Cant	29	2
Cant	29	3
Cant	29	4
Cant	29	5
Cant	29	6
Cant	29	7
Cant	29	8
Cant	29	9
Cant	29	10
Cant	29	11
Cant	29	12
Cant	29	13
Cant	29	14
Cant	29	15
Cant	29	16
Cant	29	17
Cant	29	18
Cant	29	19
Cant	29	20
Cant	29	21
Cant	29	22
Cant	29	23
Cant	29	24
Cant	29	25
Cant	29	26
Cant	29	27
Cant	29	28
Cant	29	29
Cant	29	30
Cant	30	1
Cant	30	2
Cant	30	3
Cant	30	4
Cant	30	5
Cant	30	6
Cant	30	7
Cant	30	8
Cant	30	9
Cant	30	10
Cant	30	11
Cant	30	12
Cant	30	13
Cant	30	14
Cant	30	15
Cant	30	16
Cant	30	17
Cant	30	18
Cant	30	19
Cant	30	20
Cant	30	21
Cant	30	22
Cant	30	23
Cant	30	24
Cant	30	25
Cant	30	26
Cant	30	27
Cant	30	28
Cant	30	29
Cant	30	30
Cant	31	1
Cant	31	2
Cant	31	3
Cant	31	4
Cant	31	5
Cant	31	6
Cant	31	7
Cant	31	8
Cant	31	9
Cant	31	10
Cant	31	11
Cant	31	12
Cant	31	13
Cant	31	14
Cant	31	15
Cant	31	16
Cant	31	17
Cant	31	18
Cant	31	19
Cant	31	20
Cant	31	21
Cant	31	22
Cant	31	23
Cant	31	24
Cant	31	25
Cant	31	26
Cant	31	27
Cant	31	28
Cant

0.7175643087583016	0.3981504458990962	2	10
0.7332679051559158	0.3736546301607716	2	11
0.7472178993148311	0.3678245645634487	2	12
0.7598520958361085	0.36002079419518296	2	13
0.7703873746337294	0.35200431247789743	2	14
0.7827121728052486	0.33851170745793835	2	15
0.7914808457306841	0.31887623631197015	2	16
0.8010837671100433	0.30373182002914734	2	17
0.8058154258711203	0.29560395552576657	2	18
0.8121726096093367	0.2868761560494536	2	19
0.8189954770485784	0.27968719092102756	2	20
0.8240671256553205	0.27189823153393533	2	21
0.8261408212810801	0.2693946775099222	2	22
0.8298838684744716	0.2629670397510645	2	23
0.8316164556696666	0.2598555806129256	2	24
0.8321952956907683	0.2587125392359445	2	25
0.8329849733763647	0.2576425007381701	2	26
0.8332853228955293	0.2540805615445968	2	27
0.8337119216579093	0.25245159965088027	2	28
0.8332637749347398	0.250231351619446	2	29
0.833876474309637	0.24854764942584795	2	30
0.4060476502943885	0.34152736064141687	3	1
0.5723935535200051	0.4752291313121011	3	2
0.62

0.8939213217709336	0.39352901818823216	8	22
0.8963691212580369	0.3890825836511237	8	23
0.8983499618505582	0.386088109962456	8	24
0.8997209950578133	0.38435119563844655	8	25
0.9007357708325672	0.38145630414138065	8	26
0.9014679708446179	0.37646200748890846	8	27
0.9022025739348855	0.3751027165034295	8	28
0.9029298347670162	0.374608199380015	8	29
0.9032667855395572	0.3736792652363331	8	30
0.47408167617943886	0.409184380097911	9	1
0.6030005759241384	0.5024890106795952	9	2
0.6319148594669335	0.5089072054684654	9	3
0.6426327529382854	0.5177709827083696	9	4
0.6564351077631366	0.5110743869457137	9	5
0.669320307420527	0.49564551234740395	9	6
0.6862542286966167	0.489034060423328	9	7
0.7036347569919625	0.4866035136179272	9	8
0.725160468396114	0.4860909685863951	9	9
0.7472259683563773	0.4785452815226898	9	10
0.7711261533683028	0.4707230227317636	9	11
0.7919724807890686	0.46592072717443456	9	12
0.8116861443163289	0.4595955175065789	9	13
0.8286561412853093	0.45245679590361876	9	14
0.8433803630752017

0.9138984140858138	0.38225565779393156	14	30
0.47809381752040314	0.41296139503316087	15	1
0.6074687017619858	0.5040145432313439	15	2
0.6322321581207774	0.5096975486195015	15	3
0.6427274424062115	0.5191541683918403	15	4
0.6575312479183956	0.5189173069392007	15	5
0.6701844708115183	0.5120777899090072	15	6
0.6863393396142844	0.5061361286264042	15	7
0.7046630676782597	0.5002538165776138	15	8
0.7270360516969923	0.4893836815066298	15	9
0.7495598756436698	0.48563758499879595	15	10
0.7736861544274716	0.4799356246029003	15	11
0.7945636951520727	0.47285750818029304	15	12
0.8146977115617191	0.46600767158180434	15	13
0.8325783303272922	0.4576749831708673	15	14
0.8483149312114023	0.4495387491727233	15	15
0.862207587628447	0.43861362706351015	15	16
0.8738226385685595	0.42831753007440965	15	17
0.8830397993479066	0.41971093317951036	15	18
0.8901886779044302	0.4126156622918916	15	19
0.8961459401143215	0.40372389433817946	15	20
0.9008651050881383	0.3988207928012927	15	21
0.9047129016664168	0.39468230567

...

0.9390555331833171	0.6301178927501299	23	15
0.9451799800124473	0.628606616013091	23	16
0.9489945021984241	0.62765719838648	23	17
0.9515462355102715	0.6284523972598781	23	18
0.9536664833323039	0.626595253531778	23	19
0.9546592277595152	0.6285748634217307	23	20
0.9558225656132358	0.6283186924760671	23	21
0.9562616767318406	0.6273114103595796	23	22
0.9564758812922989	0.6280665263402232	23	23
0.9568514980045549	0.6274980935400811	23	24
0.9571342202375177	0.6266713886326276	23	25
0.9570858166896571	0.627891664273416	23	26
0.9568953935656804	0.6263945453561902	23	27
0.9573522013336188	0.6285668326414162	23	28
0.9571798982516684	0.6272702752733234	23	29
0.9571720786230572	0.6300058675910152	23	30
0.4751959032736399	0.41273496712112634	24	1
0.6092714328163752	0.5083230985466362	24	2
0.6634283976008153	0.5460012342067128	24	3
0.7020196846380962	0.5658381875019411	24	4
0.7330836335729214	0.5803549224481597	24	5
0.7630524253749817	0.5967213692868072	24	6
0.792235448215215	0.6064356856133453	24	7


0.958244426699382	0.6309485152019936	29	24
0.958509524999624	0.630672187247389	29	25
0.958508671148086	0.6320709854112105	29	26
0.9583625537100074	0.6310371244577865	29	27
0.9587649556079617	0.6321808611673024	29	28
0.9586080298520064	0.6306730198592305	29	29
0.9586658612190898	0.6337855139178886	29	30
0.4736078638172442	0.41093913739463095	30	1
0.6081674627497593	0.5073993741106358	30	2
0.6634923883030123	0.5454992278740198	30	3
0.7021839451067409	0.5666816336086938	30	4
0.7329946404099986	0.5811664495772055	30	5
0.7636279343206259	0.5984449862651164	30	6
0.7933587000961793	0.6082036864729208	30	7
0.8221656550394786	0.6123143303705276	30	8
0.8476992985573142	0.619308040379016	30	9
0.8715465242398313	0.6228333420132389	30	10
0.8925590966436434	0.6259003265385246	30	11
0.9094992738841274	0.6275860047159623	30	12
0.9227562433450991	0.6291566784060743	30	13
0.9330497954291419	0.6296374064899435	30	14
0.9409044852270624	0.6331141630992843	30	15
0.9468483230379505	0.6324337755946712	30	16
0

0.6634530354299428	0.5452405705911632	36	3
0.7020949776572147	0.566788312628683	36	4
0.7333153465944762	0.5804647110708202	36	5
0.7637723458138781	0.5973287634352533	36	6
0.7936663323833958	0.6082313816392131	36	7
0.8230510566110725	0.613513477185063	36	8
0.8489494322901602	0.6206366487155353	36	9
0.8731141228716824	0.6239361019750164	36	10
0.89380390302757	0.6266168215794699	36	11
0.9107147282000405	0.6282851390527553	36	12
0.9238703016556336	0.629222986987844	36	13
0.9341384525976657	0.6301899587341931	36	14
0.9419521517570764	0.6323738169823522	36	15
0.9476795687983597	0.6321967892625555	36	16
0.9514208698697167	0.6311142290397904	36	17
0.954185217760555	0.6319143839972443	36	18
0.9558692980824582	0.6295444051616865	36	19
0.9572410959957529	0.6330804335099179	36	20
0.9581576215402212	0.6307101060252659	36	21
0.9586119599723423	0.629956336171051	36	22
0.9588521623544766	0.6326280420038879	36	23
0.9591976014583203	0.6317144679194076	36	24
0.9593730535159115	0.6310021659438174	36	25
0.

0.9105822416272972	0.6285800815698075	42	12
0.9239887832298654	0.6295728814412637	42	13
0.9345107089411432	0.6306681321363369	42	14
0.9423226324994532	0.6323030004989298	42	15
0.9481713419856735	0.6329241023200101	42	16
0.9520157225723498	0.6315895108280731	42	17
0.9548401336902621	0.6320845465360933	42	18
0.9565980342449205	0.6303038211596865	42	19
0.957969263493718	0.6332600076138999	42	20
0.9589219846444972	0.6318818631236379	42	21
0.9593601891402684	0.6313316204155206	42	22
0.9596460127936082	0.6339735943814024	42	23
0.9600130566132139	0.632646597424873	42	24
0.9601536851869829	0.6312539848779399	42	25
0.960355013517186	0.632688158978028	42	26
0.960170496146915	0.632036381488791	42	27
0.9606701631151849	0.6331670368625425	42	28
0.9604638303118972	0.6310092099779748	42	29
0.9604686778198316	0.6342005416164752	42	30
0.47401223124580805	0.4115445201794412	43	1
0.6084456833062202	0.5078104172560153	43	2
0.6627994544450388	0.5431544245345292	43	3
0.7021152550993252	0.5668270761399371	43

0.959225346005439	0.6326089392451575	48	21
0.9597382939861239	0.6323603603332963	48	22
0.9600645392819722	0.6348801917839026	48	23
0.9604036520959828	0.6330138858856191	48	24
0.9605419699566442	0.6321832165844468	48	25
0.9607809383378749	0.6336365452524619	48	26
0.9605676455879484	0.6328136888013177	48	27
0.9610947818193529	0.634020440290713	48	28
0.9608792334670869	0.6321324546504538	48	29
0.9609187720465521	0.6351695163503432	48	30
0.4728887664297414	0.410814716898925	49	1
0.6079009573199805	0.5076761216987375	49	2
0.6628116832964916	0.5430922626707912	49	3
0.7019756532184676	0.5672360073931872	49	4
0.7332049957417371	0.5801016837060193	49	5
0.7636722028714826	0.5972550693492458	49	6
0.793790882385523	0.6075048227093313	49	7
0.8230996611810237	0.6143355539303698	49	8
0.8493547897630113	0.6217090116457851	49	9
0.8735881395699561	0.6239064984730152	49	10


### 8) Применяем функции обработки данных, чистим тестовые данные

In [ ]:
test = pd.read_csv('input/test.csv')
test = prepare_data(test)

### 9) Делаем предсказание на тесте

In [ ]:
test['Price'] = evaluate_model(test, calculate_r2='No')

### 10) Записываем предсказания в файл

In [ ]:
test.loc[:, ['Id', 'Price']].to_csv('VVashchenkov_predictions.csv', index=None)